In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import altair as alt

In [2]:
county_codes = ['135', '063', '183', '037']
county_names = ['Orange', 'Durham', 'Wake', 'Chatham']

In [27]:
tracts = gpd.read_file('nc-income/tl_2020_37_tract.zip')
tracts = tracts.loc[tracts.COUNTYFP.isin(county_codes)]

income_data = pd.read_csv('nc-income/ACSDT5Y2021.B19013-Data.csv').iloc[:,0:3]
income_data = income_data.loc[income_data['Geography'].str[11:14].isin(county_codes)]
income_data.head(2)

Geography                               Geographic Area Name  \
370  1400000US37037020103  Census Tract 201.03, Chatham County, North Car...   
371  1400000US37037020104  Census Tract 201.04, Chatham County, North Car...   

    Estimate!!Median household income in the past 12 months (in 2021 inflation-adjusted dollars)  
370                                             160938                                            
371                                             130167

In [28]:
income_data['GEOID'] = income_data['Geography'].str[-11:]
tracts = tracts.merge(income_data, on='GEOID', how='left')
tracts.head(2)

STATEFP COUNTYFP TRACTCE        GEOID    NAME             NAMELSAD  MTFCC  \
0      37      135  012202  37135012202  122.02  Census Tract 122.02  G5020   
1      37      135  011902  37135011902  119.02  Census Tract 119.02  G5020   

  FUNCSTAT    ALAND  AWATER     INTPTLAT      INTPTLON  \
0        S  5573178   17211  +35.8872108  -079.0736819   
1        S  4216873  195248  +35.9441900  -079.0304855   

                                            geometry             Geography  \
0  POLYGON ((-79.08302 35.88147, -79.08300 35.881...  1400000US37135012202   
1  POLYGON ((-79.04298 35.93477, -79.04287 35.934...  1400000US37135011902   

                                Geographic Area Name  \
0  Census Tract 122.02, Orange County, North Caro...   
1  Census Tract 119.02, Orange County, North Caro...   

  Estimate!!Median household income in the past 12 months (in 2021 inflation-adjusted dollars)  
0                                              95089                                            
1                                             106667

In [29]:
tracts = tracts.rename(columns={tracts.columns[-1]:'mhi'})

In [42]:
base = alt.Chart(tracts).mark_geoshape(
    stroke='black',
    fill='lightgrey'
).encode().project(
    'albersUsa'
).properties(
    height=600,
    width=800
)

In [45]:
choro = alt.Chart(tracts).mark_geoshape(
    stroke='black'
).encode(
    alt.Color('mhi:Q', scale=alt.Scale(scheme='purplebluegreen'), title='Median Household Income'),
    tooltip=['Geographic Area Name:N','mhi:Q']
).project('albersUsa').properties(
    height=600,
    width=800
)
base + choro

alt.LayerChart(...)